제미나이 API를 사용하여 인공지능에게 유튜브 동영상을 묘사하거나 요약하라는 작업을 지시할 수 있습니다. 하지만 문제가 하나 있습니다. 현재 구글은 구글 클라우드 스토리지(Google Cloud Storage, GCS)나 File API(제미나이 인식용 임시 파일 저장소)에 올라가 있는 영상만 제미나이를 통해 인식하도록 구성해 놓았습니다. 따라서 영상을 인식하려면 ①영상 다운로드 → ② 영상 업로드 → ③ 영상 인식이라는 과정이 필요한데, 편리한 사용을 위해 이 3가지 과정을 파이프라인(Pipeline)으로 자동화하는 것이 좋습니다. 이번 절에서는 File API를 사용해 유튜브 동영상을 인식하는 방법을 다루면서, 위의 단계를 파이프라인으로 만드는 방법도 함께 알아보겠습니다.

몇 년 전 큰 화제를 모았던 “Feel the Rhythm of Korea” 시리즈의 <서울 편> 동영상으로 실습하겠습니다. 

다음 순서대로 제미나이가 유튜브 동영상을 인식하게 하겠습니다. 1) 영상을 로컬 컴퓨터로 다운로드 2) 다운로드된 영상을 File API를 통해 업로드 3) 제미나이 API로 영상 인식 4) 로컬 컴퓨터와 File API에서 영상 삭제

In [4]:
import os
import google.generativeai as genai
genai.configure(api_key=os.getenv("GOOGLE_API_KEY"))

# download

In [1]:
#!pip install pytubefix

In [2]:
from pytubefix import YouTube
url = "https://www.youtube.com/watch?v=i-E7NiyRDa0"

yt = YouTube(url) # YouTube 객체 생성
stream = yt.streams.get_highest_resolution() # 가장 높은 해상도의 스트림 선택

# 동영상 다운로드
file_path = stream.download(output_path="./videos")


# Upload 

File API

제미나이 API를 사용할 때 텍스트, 이미지, 오디오 등 멀티모달 파일을 프롬프트에 포함시키려면 파일을 저장할 수 있는 별도의 공간이 필요합니다. 기존에는 Google Cloud Storage(GCS)에 파일을 업로드한 후 제미나이 API에서 참조하는 방식을 사용했습니다. 그러나 이 방법은 구글 클라우드 플랫폼의 스토리지 서비스를 사용해야 하는 번거로움이 따랐고 Vertex AI 플랫폼을 사용해야만 했습니다. File API는 이러한 불편함을 해소하기 위해 2024년 4월 처음 도입됐습니다.

File API를 사용하면 제미나이 API와 동일한 인터페이스로 파일을 업로드, 조회, 삭제할 수 있으므로 GCS를 별도로 사용할 필요가 없습니다. 또한 File API는 제미나이 API와 통합되어 있어 업로드한 파일을 프롬프트에 쉽게 포함시킬 수 있습니다. 이를 통해 개발자는 멀티모달 입력을 보다 간편하게 처리할 수 있습니다.

File API의 또 다른 장점은 무료로 제공된다는 점입니다. 제미나이 API를 사용할 수 있는 모든 지역에서 추가 비용 없이 File API를 사용할 수 있으므로 비용 부담을 줄일 수 있습니다. 다만 API 키를 통해 업로드된 파일에 접근할 수 있으므로 키 관리에 주의가 필요합니다.



In [5]:
import google.generativeai as genai

uploaded_file = genai.upload_file(path=file_path)
print("uploaded_file.uri:", uploaded_file.uri)


uploaded_file.uri: https://generativelanguage.googleapis.com/v1beta/files/vhtljv3dsvz7


In [6]:
import IPython.display  # 동영상 플레이어 출력을 위해 추가

model = genai.GenerativeModel(model_name="gemini-1.5-flash")
prompt = """
유튜브를 보고 아래에 답하세요.
- 영상에 등장하는 춤을 추는 인물은 몇 명인가요?
- 각각의 인물에 대한 특징을 짧게 기술하세요.
"""
contents = [prompt, uploaded_file]
responses = model.generate_content(contents, stream=True, request_options={"timeout": 60*2})

IPython.display.display(IPython.display.Video(file_path, width=800 ,embed=True))
for response in responses:
    print(response.text.strip(), end="")


영상에는 춤을 추는 인물이 7명 등장합니다.* 빨간색 옷에 빨간 모자를쓴 인물: 가장 눈에 띄는 인물로, 다양한 장소에서 춤을 선보입니다. 
* 흰색 옷에흰색 모자를 쓴 인물: 빨간색 옷을 입은 인물과 함께 춤을 추며, 밝은 표정으로 춤을 즐기는 모습이 인상적입니다.
* 검은색 옷에 검은색 모자를 쓴 인물: 춤을 추는 움직임이 강렬하고,시크한 느낌을 줍니다. 
* 녹색 옷을 입은 인물: 춤을 출 때 다양한 표정을 지으며, 유머러스한 느낌을 자아냅니다.* 분홍색 옷을 입은 인물: 활발한 춤을 선보이며, 춤을 즐기는 모습이 보기 좋습니다.
* 파란색 옷을 입은 인물: 빨간색 옷을 입은 인물과 함께 춤을 추며, 흥겨운 분위기를 더합니다.
* 전통 의상을 입은 인물: 춤을 추는 인물들과 어울려서, 독특한 분위기를 연출합니다.

In [7]:
import  os

if os.path.exists(file_path):
      os.remove(file_path)

uploaded_file.delete()